In [1]:
import pandas as pd
import numpy as np
import folium
import lxml
import requests
import re
import xlrd
from geopy.geocoders import Nominatim
from pandas.io.json import json_normalize
# import k-means from clustering stage
from sklearn.cluster import KMeans

In [2]:
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
df_postal = pd.read_html(url)[0]
df_postal.dropna(inplace=True)

In [3]:
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: XO1BZSS2U14NBFS5W2PZO04I33SBHZIOROOSRYBZ1DOTEATE
CLIENT_SECRET:UDJB3D2DXGRBW4PAXALLLI2U0LYF5BCQLOZDEECIYNQPNX1M


### Supporting functions

In [4]:
# helper function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

#function to sort according venue
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

#helper function to process an address
def get_location(address):
    geolocator = Nominatim(user_agent="toronto")
    location = geolocator.geocode(address)
    center_latitude = location.latitude
    center_longitude = location.longitude
    temp_list = []
    radius = 500
    LIMIT = 100
    foursquare_url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    center_latitude, 
    center_longitude, 
    radius, 
    LIMIT)
    
    # make the GET request
    results = requests.get(foursquare_url).json()["response"]['groups'][0]['items']
        
    # return only relevant information for each nearby venue
    temp_list.extend([(
            address, 
            center_latitude, 
            center_longitude, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
        
    return temp_list

In [5]:
df_postal

Postal Code           Borough  \
0           M1A      Not assigned   
1           M2A      Not assigned   
2           M3A        North York   
3           M4A        North York   
4           M5A  Downtown Toronto   
..          ...               ...   
175         M5Z      Not assigned   
176         M6Z      Not assigned   
177         M7Z      Not assigned   
178         M8Z         Etobicoke   
179         M9Z      Not assigned   

                                          Neighborhood  
0                                         Not assigned  
1                                         Not assigned  
2                                            Parkwoods  
3                                     Victoria Village  
4                            Regent Park, Harbourfront  
..                                                 ...  
175                                       Not assigned  
176                                       Not assigned  
177                                       Not assigned  
178  Mimico NW, The Queensway West, South of Bloor,...  
179                                       Not assigned  

[180 rows x 3 columns]

# Part 1
### Scraped content with not assigned areas cleaned out

In [6]:
type(df_postal)
df_postal = df_postal[~df_postal.Borough.str.endswith("Not assigned") | ~df_postal.Neighborhood.str.endswith("Not assigned")]
df_postal.reset_index(drop=True)

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
..          ...               ...   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                          Neighborhood  
0                                            Parkwoods  
1                                     Victoria Village  
2                            Regent Park, Harbourfront  
3                     Lawrence Manor, Lawrence Heights  
4          Queen's Park, Ontario Provincial Government  
..                                                 ...  
98       The Kingsway, Montgomery Road, Old Mill North  
99                                Church and Wellesley  
100  Business reply mail Processing Centre, South C...  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  
102  Mimico NW, The Queensway West, South of Bloor,...  

[103 rows x 3 columns]

In [7]:
df_postal.shape

(103, 3)

# Part 2
### All the postal codes with coordinates

In [8]:
coordinates_url = "./Geospatial_Coordinates.csv"
df_coordinates = pd.read_csv(coordinates_url) 

In [9]:
df_coordinates

Postal Code   Latitude  Longitude
0           M1B  43.806686 -79.194353
1           M1C  43.784535 -79.160497
2           M1E  43.763573 -79.188711
3           M1G  43.770992 -79.216917
4           M1H  43.773136 -79.239476
..          ...        ...        ...
98          M9N  43.706876 -79.518188
99          M9P  43.696319 -79.532242
100         M9R  43.688905 -79.554724
101         M9V  43.739416 -79.588437
102         M9W  43.706748 -79.594054

[103 rows x 3 columns]

In [10]:
df_postal_codes = pd.merge(df_postal, df_coordinates, on='Postal Code')
df_postal_codes

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
..          ...               ...   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
1                                     Victoria Village  43.725882 -79.315572  
2                            Regent Park, Harbourfront  43.654260 -79.360636  
3                     Lawrence Manor, Lawrence Heights  43.718518 -79.464763  
4          Queen's Park, Ontario Provincial Government  43.662301 -79.389494  
..                                                 ...        ...        ...  
98       The Kingsway, Montgomery Road, Old Mill North  43.653654 -79.506944  
99                                Church and Wellesley  43.665860 -79.383160  
100  Business reply mail Processing Centre, South C...  43.662744 -79.321558  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509  
102  Mimico NW, The Queensway West, South of Bloor,...  43.628841 -79.520999  

[103 rows x 5 columns]

In [41]:
df_postal_codes.shape

(103, 5)

# Part 3
### Filter out Neighborhoods which contain 'park' in their name

In [11]:
#Get list of boroughs to analyze
df_borough_list = df_postal_codes[df_postal_codes["Neighborhood"].str.contains('park',flags=re.IGNORECASE, regex=True)].groupby('Borough').apply(list).reset_index()["Borough"]
df_borough_list

0     Central Toronto
1    Downtown Toronto
2           East York
3           Etobicoke
4          North York
5         Scarborough
6        West Toronto
Name: Borough, dtype: object

In [12]:
#Get list of neighborhoods in the boroughs
df_neighborhood_list = df_postal_codes[df_postal_codes["Neighborhood"].str.contains('park',flags=re.IGNORECASE, regex=True)]
df_neighborhood_list

Postal Code           Borough  \
0           M3A        North York   
2           M5A  Downtown Toronto   
4           M7A  Downtown Toronto   
8           M4B         East York   
11          M9B         Etobicoke   
20          M5E  Downtown Toronto   
29          M4H         East York   
34          M3J        North York   
38          M1K       Scarborough   
43          M6K      West Toronto   
49          M6L        North York   
55          M5M        North York   
61          M4N   Central Toronto   
65          M1P       Scarborough   
68          M5P   Central Toronto   
69          M6P      West Toronto   
73          M4R   Central Toronto   
75          M6R      West Toronto   
83          M4T   Central Toronto   
84          M5T  Downtown Toronto   
86          M4V   Central Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
2                            Regent Park, Harbourfront  43.654260 -79.360636  
4          Queen's Park, Ontario Provincial Government  43.662301 -79.389494  
8                      Parkview Hill, Woodbine Gardens  43.706397 -79.309937  
11   West Deane Park, Princess Gardens, Martin Grov...  43.650943 -79.554724  
20                                         Berczy Park  43.644771 -79.373306  
29                                    Thorncliffe Park  43.705369 -79.349372  
34                     Northwood Park, York University  43.767980 -79.487262  
38         Kennedy Park, Ionview, East Birchmount Park  43.727929 -79.262029  
43        Brockton, Parkdale Village, Exhibition Place  43.636847 -79.428191  
49            North Park, Maple Leaf Park, Upwood Park  43.713756 -79.490074  
55                   Bedford Park, Lawrence Manor East  43.733283 -79.419750  
61                                       Lawrence Park  43.728020 -79.388790  
65   Dorset Park, Wexford Heights, Scarborough Town...  43.757410 -79.273304  
68     Forest Hill North & West, Forest Hill Road Park  43.696948 -79.411307  
69                       High Park, The Junction South  43.661608 -79.464763  
73                   North Toronto West, Lawrence Park  43.715383 -79.405678  
75                              Parkdale, Roncesvalles  43.648960 -79.456325  
83                         Moore Park, Summerhill East  43.689574 -79.383160  
84           Kensington Market, Chinatown, Grange Park  43.653206 -79.400049  
86   Summerhill West, Rathnelly, South Hill, Forest...  43.686412 -79.400049  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509  
102  Mimico NW, The Queensway West, South of Bloor,...  43.628841 -79.520999

### Addtional Toronto data from: 
 https://open.toronto.ca/dataset/wellbeing-toronto-demographics/
 https://github.com/jasonicarter/toronto-geojson

In [13]:
#Load additional data
geojson_file='./toronto_crs84.geojson.txt'
demographic_file='./wellbeing-toronto-demographics.xlsx'
df_demographics = pd.read_excel(demographic_file,
                     sheet_name='RawData-Ref Period 2011',header=1)


In [14]:
df_demographics

Neighbourhood  Neighbourhood Id  Total Area  \
0               West Humber-Clairville                 1       30.09   
1    Mount Olive-Silverstone-Jamestown                 2        4.60   
2         Thistletown-Beaumond Heights                 3        3.40   
3                      Rexdale-Kipling                 4        2.50   
4                     Elms-Old Rexdale                 5        2.90   
..                                 ...               ...         ...   
135                          West Hill               136        9.60   
136                             Woburn               137       12.20   
137                      Eglinton East               138        3.20   
138                Scarborough Village               139        3.10   
139                          Guildwood               140        3.80   

     Total Population  Pop - Males  Pop - Females  Pop 0 - 4 years  \
0               34100        17095          17000             1865   
1               32790        16015          16765             2575   
2               10140         4920           5225              575   
3               10485         5035           5455              495   
4                9550         4615           4935              670   
..                ...          ...            ...              ...   
135             26550        12560          14000             1575   
136             53350        26005          27330             3485   
137             22830        10580          12240             1555   
138             16615         7825           8790             1200   
139              9815         4550           5270              370   

     Pop 5 - 9 years  Pop 10 - 14 years  Pop 15 -19 years  ...  \
0               1950               2155              2550  ...   
1               2535               2555              2620  ...   
2                580                670               675  ...   
3                520                570               665  ...   
4                720                720               725  ...   
..               ...                ...               ...  ...   
135             1550               1820              2055  ...   
136             3415               3400              3575  ...   
137             1500               1500              1545  ...   
138             1140               1150              1240  ...   
139              440                485               565  ...   

        Language - Chinese     Language - Italian     Language - Korean  \
0                      475                    925                    95   
1                      275                    750                    60   
2                       95                    705                    35   
3                       95                    475                    30   
4                       90                    510                    55   
..                     ...                    ...                   ...   
135                    575                    330                    60   
136                   3560                    430                   125   
137                    915                    255                    55   
138                    330                    160                    35   
139                    185                    110                    30   

        Language - Persian (Farsi)     Language - Portuguese  \
0                              160                       205   
1                              350                       115   
2                              115                       105   
3                               95                       145   
4                              285                        80   
..                             ...                       ...   
135                            445                        90   
136                           1070                       180   
137                            305               

In [15]:
df_demographics.dtypes

Neighbourhood                     object
Neighbourhood Id                   int64
Total Area                       float64
Total Population                   int64
Pop - Males                        int64
Pop - Females                      int64
Pop 0 - 4 years                    int64
Pop 5 - 9 years                    int64
Pop 10 - 14 years                  int64
Pop 15 -19 years                   int64
Pop 20 - 24 years                  int64
Pop  25 - 29 years                 int64
Pop 30 - 34 years                  int64
Pop 35 - 39 years                  int64
Pop 40 - 44 years                  int64
Pop 45 - 49 years                  int64
Pop 50 - 54 years                  int64
Pop 55 - 59 years                  int64
Pop 60 - 64 years                  int64
Pop 65 - 69 years                  int64
Pop 70 - 74 years                  int64
Pop 75 - 79 years                  int64
Pop 80 - 84 years                  int64
Pop 85 years and over              int64
Seniors 55 and o

In [16]:
venue_list=[]
for row in df_borough_list:
    venue_list.extend(get_location(row))

df_venues = pd.DataFrame(venue_list)

In [17]:
df_venues

0          1          2                         3  \
0    Central Toronto  43.653482 -79.383935          Downtown Toronto   
1    Central Toronto  43.653482 -79.383935    Nathan Phillips Square   
2    Central Toronto  43.653482 -79.383935                    Indigo   
3    Central Toronto  43.653482 -79.383935              Chatime 日出茶太   
4    Central Toronto  43.653482 -79.383935  Textile Museum of Canada   
..               ...        ...        ...                       ...   
322     West Toronto  43.653482 -79.383935      Pantages Hotel & Spa   
323     West Toronto  43.653482 -79.383935               Tim Hortons   
324     West Toronto  43.653482 -79.383935     Pantages Lounge & Bar   
325     West Toronto  43.653482 -79.383935               Tim Hortons   
326     West Toronto  43.653482 -79.383935               Blaze Pizza   

             4          5                6  
0    43.653232 -79.385296     Neighborhood  
1    43.652270 -79.383516            Plaza  
2    43.653515 -79.380696        Bookstore  
3    43.655542 -79.384684  Bubble Tea Shop  
4    43.654396 -79.386500       Art Museum  
..         ...        ...              ...  
322  43.654498 -79.379035            Hotel  
323  43.655212 -79.380063      Coffee Shop  
324  43.654493 -79.379000     Cocktail Bar  
325  43.653690 -79.378356      Coffee Shop  
326  43.656518 -79.380015      Pizza Place  

[327 rows x 7 columns]

In [18]:
df_venues.columns = ["Borough","area_lat","area_long","name","lat","lng","categories"]

In [19]:
df_venues.groupby('Borough').count()

area_lat  area_long  name  lat  lng  categories
Borough                                                          
Central Toronto         77         77    77   77   77          77
Downtown Toronto        97         97    97   97   97          97
East York               12         12    12   12   12          12
Etobicoke               10         10    10   10   10          10
North York               4          4     4    4    4           4
Scarborough             50         50    50   50   50          50
West Toronto            77         77    77   77   77          77

In [20]:
print('There are {} uniques categories.'.format(len(df_venues['categories'].unique())))

There are 96 uniques categories.


### One hot encoding of categories

In [21]:
# one hot encoding
df_onehotenc = pd.get_dummies(df_venues[['categories']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
df_onehotenc['Borough'] = df_venues['Borough'] 

# move neighborhood column to the first column
fixed_columns = [df_onehotenc.columns[-1]] + list(df_onehotenc.columns[:-1])
df_onehotenc = df_onehotenc[fixed_columns]

df_onehotenc.head()

Borough  American Restaurant  Arcade  Art Gallery  Art Museum  \
0  Central Toronto                    0       0            0           0   
1  Central Toronto                    0       0            0           0   
2  Central Toronto                    0       0            0           0   
3  Central Toronto                    0       0            0           0   
4  Central Toronto                    0       0            0           1   

   Bakery  Bank  Bar  Beach  Beer Bar  ...  Tanning Salon  Tea Room  \
0       0     0    0      0         0  ...              0         0   
1       0     0    0      0         0  ...              0         0   
2       0     0    0      0         0  ...              0         0   
3       0     0    0      0         0  ...              0         0   
4       0     0    0      0         0  ...              0         0   

   Thai Restaurant  Theater  Thrift / Vintage Store  Train Station  \
0                0        0                       0              0   
1                0        0                       0              0   
2                0        0                       0              0   
3                0        0                       0              0   
4                0        0                       0              0   

   Vegetarian / Vegan Restaurant  Video Game Store  Vietnamese Restaurant  \
0                              0                 0                      0   
1                              0                 0                      0   
2                              0                 0                      0   
3                              0                 0                      0   
4                              0                 0                      0   

   Women's Store  
0              0  
1              0  
2              0  
3              0  
4              0  

[5 rows x 97 columns]

In [22]:
df_grouped = df_onehotenc.groupby('Borough').mean().reset_index()

In [23]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Borough']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Borough'] = df_grouped['Borough']

for ind in np.arange(df_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(df_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Borough   1st Most Common Venue 2nd Most Common Venue  \
0   Central Toronto             Coffee Shop        Clothing Store   
1  Downtown Toronto             Coffee Shop        Clothing Store   
2         East York  Thrift / Vintage Store   American Restaurant   
3         Etobicoke            Skating Rink                  Café   
4        North York             Pizza Place           Coffee Shop   

      3rd Most Common Venue      4th Most Common Venue 5th Most Common Venue  \
0                Restaurant        American Restaurant                  Café   
1                Restaurant                      Hotel                 Diner   
2          Sushi Restaurant                 Donut Shop           Music Store   
3              Intersection                Coffee Shop            Restaurant   
4  Mediterranean Restaurant  Middle Eastern Restaurant     Fish & Chips Shop   

  6th Most Common Venue      7th Most Common Venue 8th Most Common Venue  \
0                 Hotel                      Plaza                 Diner   
1                  Café  Middle Eastern Restaurant               Theater   
2    Seafood Restaurant               Burger Joint                Lawyer   
3        Clothing Store             Farmers Market     Convenience Store   
4        Cosmetics Shop           Department Store          Dessert Shop   

  9th Most Common Venue 10th Most Common Venue  
0    Seafood Restaurant         Cosmetics Shop  
1    Chinese Restaurant                  Plaza  
2          Optical Shop                 Bakery  
3                 Hotel          Grocery Store  
4                 Diner             Donut Shop

### Grouping the categories into either food area, shopping, music/theater or other

In [24]:
df_venues["CATEGORY GROUP"]="Other"
df_venues.loc[df_venues["categories"].str.contains('hortons|cafe|café|bar|restaurant|diner|pub',flags=re.IGNORECASE, regex=True),["CATEGORY GROUP"]]="Food/Beverage"
df_venues.loc[df_venues["categories"].str.contains('shop|store',flags=re.IGNORECASE, regex=True),["CATEGORY GROUP"]]="Mall/Specialty Store"
df_venues.loc[df_venues["categories"].str.contains('pizza|salad|ice cream|steak|tea|dessert|poke place|coffee|breakfast|smoothie', flags=re.IGNORECASE, regex=True),["CATEGORY GROUP"]]="Food/Beverage"
df_venues.loc[df_venues["categories"].str.contains('theater|music|opera|concert', flags=re.IGNORECASE, regex=True),["CATEGORY GROUP"]]="Music/Theater"
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', 200)
df_venues

Borough   area_lat  area_long                      name  \
0    Central Toronto  43.653482 -79.383935          Downtown Toronto   
1    Central Toronto  43.653482 -79.383935    Nathan Phillips Square   
2    Central Toronto  43.653482 -79.383935                    Indigo   
3    Central Toronto  43.653482 -79.383935              Chatime 日出茶太   
4    Central Toronto  43.653482 -79.383935  Textile Museum of Canada   
..               ...        ...        ...                       ...   
322     West Toronto  43.653482 -79.383935      Pantages Hotel & Spa   
323     West Toronto  43.653482 -79.383935               Tim Hortons   
324     West Toronto  43.653482 -79.383935     Pantages Lounge & Bar   
325     West Toronto  43.653482 -79.383935               Tim Hortons   
326     West Toronto  43.653482 -79.383935               Blaze Pizza   

           lat        lng       categories        CATEGORY GROUP  
0    43.653232 -79.385296     Neighborhood                 Other  
1    43.652270 -79.383516            Plaza                 Other  
2    43.653515 -79.380696        Bookstore  Mall/Specialty Store  
3    43.655542 -79.384684  Bubble Tea Shop         Food/Beverage  
4    43.654396 -79.386500       Art Museum                 Other  
..         ...        ...              ...                   ...  
322  43.654498 -79.379035            Hotel                 Other  
323  43.655212 -79.380063      Coffee Shop         Food/Beverage  
324  43.654493 -79.379000     Cocktail Bar         Food/Beverage  
325  43.653690 -79.378356      Coffee Shop         Food/Beverage  
326  43.656518 -79.380015      Pizza Place         Food/Beverage  

[327 rows x 8 columns]

In [25]:
geolocator = Nominatim(user_agent="toronto")
location = geolocator.geocode("Toronto, Canada")
center_latitude = location.latitude
center_longitude = location.longitude

In [26]:
df_demographics['NeighbourhoodWithId']=df_demographics[['Neighbourhood','Neighbourhood Id']].apply(lambda x: '%s (%s)'%(x['Neighbourhood'],x['Neighbourhood Id']), axis=1)

In [27]:
df_demographics

Neighbourhood  Neighbourhood Id  Total Area  \
0               West Humber-Clairville                 1       30.09   
1    Mount Olive-Silverstone-Jamestown                 2        4.60   
2         Thistletown-Beaumond Heights                 3        3.40   
3                      Rexdale-Kipling                 4        2.50   
4                     Elms-Old Rexdale                 5        2.90   
5        Kingsview Village-The Westway                 6        5.10   
6     Willowridge-Martingrove-Richview                 7        5.50   
7             Humber Heights-Westmount                 8        2.80   
8             Edenbridge-Humber Valley                 9        5.50   
9                   Princess-Rosethorn                10        5.20   
10      Eringate-Centennial-West Deane                11        8.60   
11                       Markland Wood                12        2.90   
12                 Etobicoke West Mall                13        1.70   
13          Islington-City Centre West                14       16.40   
14                      Kingsway South                15        2.60   
15                 Stonegate-Queensway                16        7.90   
16                              Mimico                17        6.90   
17                         New Toronto                18        3.50   
18                         Long Branch                19        2.30   
19                           Alderwood                20        5.00   
20                       Humber Summit                21        7.90   
21                          Humbermede                22        4.40   
22                Pelmo Park-Humberlea                23        4.20   
23                         Black Creek                24        3.40   
24              Glenfield-Jane Heights                25        5.20   
25                Downsview-Roding-CFB                26       14.90   
26             York University Heights                27       13.20   
27                              Rustic                28        2.10   
28                          Maple Leaf                29        2.50   
29                 Brookhaven-Amesbury                30        3.50   
30                  Yorkdale-Glen Park                31        5.90   
31                 Englemount-Lawrence                32        3.60   
32                        Clanton Park                33        4.20   
33                      Bathurst Manor                34        4.80   
34                 Westminster-Branson                35        3.70   
35                    Newtonbrook West                36        4.70   
36                     Willowdale West                37        2.90   
37                    Lansing-Westgate                38        5.40   
38                Bedford Park-Nortown                39        5.50   
39                St.Andrew-Windfields                40        7.30   
40   Bridle Path-Sunnybrook-York Mills                41        8.80   
41                   Banbury-Don Mills                42       10.00   
42                    Victoria Village                43        4.70   
43                     Flemingdon Park                44        2.50   
44                   Parkwoods-Donalda                45        7.50   
45                       Pleasant View                46        3.00   
46                  Don Valley Village                47        4.10   
47                   Hillcrest Village                48        5.30   
48               Bayview Woods-Steeles                49        4.10   
49                    Newtonbrook East                50        4.10   
50                     Willowdale East                51        5.00   
51                     Bayview Village                52        5.20   
52                          Henry Farm                53        2.60   
53                   O'Connor-Parkview                54        4.90   
54                    Thorncliffe Park                55        3

In [28]:
#Create chloropleth map
# create a plain toronto map
toronto_map = folium.Map(location=[center_latitude, center_longitude], zoom_start=11)
# generate choropleth map using the total immigration of each country to Canada from 1980 to 2013
toronto_map.choropleth(
    geo_data=geojson_file,
    data=df_demographics,
    columns=['NeighbourhoodWithId', 'Total Population'],
    key_on='feature.properties.AREA_NAME',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Population Density'
)

borough_colors={'Central Toronto':'#66c2a5','Downtown Toronto':'#fc8d62','East York':'#8da0cb','Etobicoke':'#e78ac3',
                'North York':'#a6d854','Scarborough':'#ffd92f','West Toronto':'#e5c494'}
for borough, lat, lng, categories, name, catgroup in zip(df_venues['Borough'], df_venues['lat'], df_venues['lng'],
                                                         df_venues['categories'], df_venues['name'], df_venues['CATEGORY GROUP']):
    label = '{}, {}, {}'.format(categories, name, borough)
    label = folium.Popup(label, parse_html=True)
    if catgroup=="Food/Beverage":
        folium.CircleMarker(
            [lat, lng],
            radius=7,
            popup=label,
            color='red',
            fill=True,
            fill_color=borough_colors[borough],
            fill_opacity=0.9,
            parse_html=False).add_to(toronto_map)
    elif catgroup=="Mall/Specialty Store":
            folium.CircleMarker(
            [lat, lng],
            radius=7,
            popup=label,
            color='blue',
            fill=True,
            fill_color=borough_colors[borough],
            fill_opacity=0.9,
            parse_html=False).add_to(toronto_map)
    elif catgroup=="Music/Theater":
            folium.CircleMarker(
            [lat, lng],
            radius=7,
            popup=label,
            color='green',
            fill=True,
            fill_color=borough_colors[borough],
            fill_opacity=0.9,
            parse_html=False).add_to(toronto_map)
    else:
            folium.CircleMarker(
            [lat, lng],
            radius=7,
            popup=label,
            color='orange',
            fill=True,
            fill_color=borough_colors[borough],
            fill_opacity=0.9,
            parse_html=False).add_to(toronto_map)
# display map
toronto_map

/Users/gquisumbing/Documents/envs/dsclass/lib/python3.7/site-packages/folium/folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [29]:
borough_colors['Central Toronto']

'#66c2a5'

In [30]:
for lat, lng, categories, name, catgroup in zip(df_venues['lat'], df_venues['lng'], df_venues['categories'], df_venues['name'], df_venues['CATEGORY GROUP']):
    print(lat,lng,name)

43.65323167517444 -79.38529600606677 Downtown Toronto
43.65227047322295 -79.38351631164551 Nathan Phillips Square
43.65351471121164 -79.38069591056922 Indigo
43.65554164147378 -79.38468427043244 Chatime 日出茶太
43.65439630500274 -79.38650010906946 Textile Museum of Canada
43.65489527525682 -79.38505238381624 Poke Guys
43.65526771691681 -79.38516506734886 Japango
43.653557 -79.3804 LUSH
43.65121797253777 -79.38355459932247 M Square Coffee Co
43.654540112988535 -79.38067738352993 CF Toronto Eaton Centre
43.654536488277245 -79.38088885547485 Crepe Delicious
43.655157467561246 -79.38650067479335 Sansotei Ramen 三草亭
43.65591027779457 -79.38064099181345 UNIQLO ユニクロ
43.650592 -79.385806 Four Seasons Centre for the Performing Arts
43.6546083 -79.3859415 DoubleTree by Hilton
43.655101567321054 -79.37976762131545 Ed Mirvish Theatre
43.65065218852629 -79.38414092873634 Bulldog On The Block
43.65491791857301 -79.3874242454196 Rolltation
43.65065642537144 -79.38161285228475 John & Sons Oyster House
43.

In [31]:
df_venues.groupby('Borough')['name'].count()

Borough
Central Toronto     77
Downtown Toronto    97
East York           12
Etobicoke           10
North York           4
Scarborough         50
West Toronto        77
Name: name, dtype: int64

In [32]:
df_grouped_clustering = df_grouped.drop('Borough', 1)
df_grouped_clustering

American Restaurant  Arcade  Art Gallery  Art Museum    Bakery      Bank  \
0             0.025974    0.00     0.000000    0.012987  0.000000  0.012987   
1             0.010309    0.00     0.010309    0.010309  0.000000  0.010309   
2             0.083333    0.00     0.000000    0.000000  0.083333  0.000000   
3             0.000000    0.00     0.000000    0.000000  0.000000  0.000000   
4             0.000000    0.00     0.000000    0.000000  0.000000  0.000000   
5             0.000000    0.06     0.000000    0.000000  0.020000  0.000000   
6             0.025974    0.00     0.000000    0.012987  0.000000  0.012987   

        Bar  Beach  Beer Bar  Bookstore  ...  Tanning Salon  Tea Room  \
0  0.000000   0.00  0.012987   0.012987  ...       0.012987  0.012987   
1  0.020619   0.00  0.010309   0.010309  ...       0.020619  0.010309   
2  0.083333   0.00  0.000000   0.000000  ...       0.000000  0.000000   
3  0.000000   0.00  0.000000   0.000000  ...       0.000000  0.000000   
4  0.000000   0.00  0.000000   0.000000  ...       0.000000  0.000000   
5  0.020000   0.06  0.000000   0.040000  ...       0.000000  0.000000   
6  0.000000   0.00  0.012987   0.012987  ...       0.012987  0.012987   

   Thai Restaurant   Theater  Thrift / Vintage Store  Train Station  \
0         0.012987  0.025974                0.000000           0.00   
1         0.000000  0.020619                0.000000           0.00   
2         0.000000  0.000000                0.166667           0.00   
3         0.000000  0.000000                0.000000           0.00   
4         0.000000  0.000000                0.000000           0.00   
5         0.020000  0.020000                0.000000           0.02   
6         0.012987  0.025974                0.000000           0.00   

   Vegetarian / Vegan Restaurant  Video Game Store  Vietnamese Restaurant  \
0                       0.012987          0.012987               0.012987   
1                       0.000000          0.010309               0.010309   
2                       0.000000          0.000000               0.000000   
3                       0.000000          0.000000               0.000000   
4                       0.000000          0.000000               0.000000   
5                       0.000000          0.020000               0.000000   
6                       0.012987          0.012987               0.012987   

   Women's Store  
0       0.012987  
1       0.010309  
2       0.000000  
3       0.000000  
4       0.000000  
5       0.000000  
6       0.012987  

[7 rows x 96 columns]

In [33]:
# set number of clusters
kclusters = 4

df_grouped_clustering = df_grouped.drop('Borough', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(df_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 2, 1, 3, 0, 2, 2], dtype=int32)

In [34]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

df_merged = df_venues

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
df_merged = df_merged.join(neighborhoods_venues_sorted.set_index('Borough'), on='Borough')

df_merged.head() # check the last columns!

Borough   area_lat  area_long                      name        lat  \
0  Central Toronto  43.653482 -79.383935          Downtown Toronto  43.653232   
1  Central Toronto  43.653482 -79.383935    Nathan Phillips Square  43.652270   
2  Central Toronto  43.653482 -79.383935                    Indigo  43.653515   
3  Central Toronto  43.653482 -79.383935              Chatime 日出茶太  43.655542   
4  Central Toronto  43.653482 -79.383935  Textile Museum of Canada  43.654396   

         lng       categories        CATEGORY GROUP  Cluster Labels  \
0 -79.385296     Neighborhood                 Other               2   
1 -79.383516            Plaza                 Other               2   
2 -79.380696        Bookstore  Mall/Specialty Store               2   
3 -79.384684  Bubble Tea Shop         Food/Beverage               2   
4 -79.386500       Art Museum                 Other               2   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0           Coffee Shop        Clothing Store            Restaurant   
1           Coffee Shop        Clothing Store            Restaurant   
2           Coffee Shop        Clothing Store            Restaurant   
3           Coffee Shop        Clothing Store            Restaurant   
4           Coffee Shop        Clothing Store            Restaurant   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0   American Restaurant                  Café                 Hotel   
1   American Restaurant                  Café                 Hotel   
2   American Restaurant                  Café                 Hotel   
3   American Restaurant                  Café                 Hotel   
4   American Restaurant                  Café                 Hotel   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                 Plaza                 Diner    Seafood Restaurant   
1                 Plaza                 Diner    Seafood Restaurant   
2                 Plaza                 Diner    Seafood Restaurant   
3                 Plaza                 Diner    Seafood Restaurant   
4                 Plaza                 Diner    Seafood Restaurant   

  10th Most Common Venue  
0         Cosmetics Shop  
1         Cosmetics Shop  
2         Cosmetics Shop  
3         Cosmetics Shop  
4         Cosmetics Shop

In [35]:
df_merged.loc[df_merged['Cluster Labels'] == 0, df_merged.columns[[1] + list(range(5, df_merged.shape[1]))]]

area_lat        lng                 categories CATEGORY GROUP  \
196  43.754326 -79.451690   Mediterranean Restaurant  Food/Beverage   
197  43.754326 -79.443507  Middle Eastern Restaurant  Food/Beverage   
198  43.754326 -79.443250                Coffee Shop  Food/Beverage   
199  43.754326 -79.450926                Pizza Place  Food/Beverage   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
196               0           Pizza Place           Coffee Shop   
197               0           Pizza Place           Coffee Shop   
198               0           Pizza Place           Coffee Shop   
199               0           Pizza Place           Coffee Shop   

        3rd Most Common Venue      4th Most Common Venue  \
196  Mediterranean Restaurant  Middle Eastern Restaurant   
197  Mediterranean Restaurant  Middle Eastern Restaurant   
198  Mediterranean Restaurant  Middle Eastern Restaurant   
199  Mediterranean Restaurant  Middle Eastern Restaurant   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
196     Fish & Chips Shop        Cosmetics Shop      Department Store   
197     Fish & Chips Shop        Cosmetics Shop      Department Store   
198     Fish & Chips Shop        Cosmetics Shop      Department Store   
199     Fish & Chips Shop        Cosmetics Shop      Department Store   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
196          Dessert Shop                 Diner             Donut Shop  
197          Dessert Shop                 Diner             Donut Shop  
198          Dessert Shop                 Diner             Donut Shop  
199          Dessert Shop                 Diner             Donut Shop

In [36]:
df_merged.loc[df_merged['Cluster Labels'] == 1, df_merged.columns[[1] + list(range(5, df_merged.shape[1]))]]

area_lat        lng              categories        CATEGORY GROUP  \
174  39.973709 -76.681856              Donut Shop  Mall/Specialty Store   
175  39.973709 -76.681358            Burger Joint                 Other   
176  39.973709 -76.685829      Seafood Restaurant         Food/Beverage   
177  39.973709 -76.681542        Sushi Restaurant         Food/Beverage   
178  39.973709 -76.681314     American Restaurant         Food/Beverage   
179  39.973709 -76.688130                  Lawyer                 Other   
180  39.973709 -76.686853            Optical Shop  Mall/Specialty Store   
181  39.973709 -76.681960             Music Store         Music/Theater   
182  39.973709 -76.681547                  Bakery                 Other   
183  39.973709 -76.681011  Thrift / Vintage Store  Mall/Specialty Store   
184  39.973709 -76.685545                     Bar         Food/Beverage   
185  39.973709 -76.684823  Thrift / Vintage Store  Mall/Specialty Store   

     Cluster Labels   1st Most Common Venue 2nd Most Common Venue  \
174               1  Thrift / Vintage Store   American Restaurant   
175               1  Thrift / Vintage Store   American Restaurant   
176               1  Thrift / Vintage Store   American Restaurant   
177               1  Thrift / Vintage Store   American Restaurant   
178               1  Thrift / Vintage Store   American Restaurant   
179               1  Thrift / Vintage Store   American Restaurant   
180               1  Thrift / Vintage Store   American Restaurant   
181               1  Thrift / Vintage Store   American Restaurant   
182               1  Thrift / Vintage Store   American Restaurant   
183               1  Thrift / Vintage Store   American Restaurant   
184               1  Thrift / Vintage Store   American Restaurant   
185               1  Thrift / Vintage Store   American Restaurant   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
174      Sushi Restaurant            Donut Shop           Music Store   
175      Sushi Restaurant            Donut Shop           Music Store   
176      Sushi Restaurant            Donut Shop           Music Store   
177      Sushi Restaurant            Donut Shop           Music Store   
178      Sushi Restaurant            Donut Shop           Music Store   
179      Sushi Restaurant            Donut Shop           Music Store   
180      Sushi Restaurant            Donut Shop           Music Store   
181      Sushi Restaurant            Donut Shop           Music Store   
182      Sushi Restaurant            Donut Shop           Music Store   
183      Sushi Restaurant            Donut Shop           Music Store   
184      Sushi Restaurant            Donut Shop           Music Store   
185      Sushi Restaurant            Donut Shop           Music Store   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
174    Seafood Restaurant          Burger Joint                Lawyer   
175    Seafood Restaurant          Burger Joint                Lawyer   
176    Seafood Restaurant          Burger Joint                Lawyer   
177    Seafood Restaurant          Burger Joint                Lawyer   
178    Seafood Restaurant          Burger Joint                Lawyer   
179    Seafood Restaurant          Burger Joint                Lawyer   
180    Seafood Restaurant          Burger Joint                Lawyer   
181    Seafood Restaurant          Burger Joint                Lawyer   
182    Seafood Restaurant          Burger Joint                Lawyer   
183    Seafood Restaurant          Burger Joint                Lawyer   
184    Seafood Restaurant          Burger Joint                Lawyer   
185    Seafood Restaurant          Burger Joint                Lawyer   

    9th Most Common Venue 10th Most Common Venue  
174          Optical Shop                 Bakery  
175          Optical Shop                 Bakery  
176          Optical Shop                 Bakery  
177          Optical Shop   

In [37]:
df_merged.loc[df_merged['Cluster Labels'] == 2, df_merged.columns[[1] + list(range(5, df_merged.shape[1]))]]

area_lat        lng       categories        CATEGORY GROUP  \
0    43.653482 -79.385296     Neighborhood                 Other   
1    43.653482 -79.383516            Plaza                 Other   
2    43.653482 -79.380696        Bookstore  Mall/Specialty Store   
3    43.653482 -79.384684  Bubble Tea Shop         Food/Beverage   
4    43.653482 -79.386500       Art Museum                 Other   
..         ...        ...              ...                   ...   
322  43.653482 -79.379035            Hotel                 Other   
323  43.653482 -79.380063      Coffee Shop         Food/Beverage   
324  43.653482 -79.379000     Cocktail Bar         Food/Beverage   
325  43.653482 -79.378356      Coffee Shop         Food/Beverage   
326  43.653482 -79.380015      Pizza Place         Food/Beverage   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0                 2           Coffee Shop        Clothing Store   
1                 2           Coffee Shop        Clothing Store   
2                 2           Coffee Shop        Clothing Store   
3                 2           Coffee Shop        Clothing Store   
4                 2           Coffee Shop        Clothing Store   
..              ...                   ...                   ...   
322               2           Coffee Shop        Clothing Store   
323               2           Coffee Shop        Clothing Store   
324               2           Coffee Shop        Clothing Store   
325               2           Coffee Shop        Clothing Store   
326               2           Coffee Shop        Clothing Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0              Restaurant   American Restaurant                  Café   
1              Restaurant   American Restaurant                  Café   
2              Restaurant   American Restaurant                  Café   
3              Restaurant   American Restaurant                  Café   
4              Restaurant   American Restaurant                  Café   
..                    ...                   ...                   ...   
322            Restaurant   American Restaurant                  Café   
323            Restaurant   American Restaurant                  Café   
324            Restaurant   American Restaurant                  Café   
325            Restaurant   American Restaurant                  Café   
326            Restaurant   American Restaurant                  Café   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                   Hotel                 Plaza                 Diner   
1                   Hotel                 Plaza                 Diner   
2                   Hotel                 Plaza                 Diner   
3                   Hotel                 Plaza                 Diner   
4                   Hotel                 Plaza                 Diner   
..                    ...                   ...                   ...   
322                 Hotel                 Plaza                 Diner   
323                 Hotel                 Plaza                 Diner   
324                 Hotel                 Plaza                 Diner   
325                 Hotel                 Plaza                 Diner   
326                 Hotel                 Plaza                 Diner   

    9th Most Common Venue 10th Most Common Venue  
0      Seafood Restaurant         Cosmetics Shop  
1      Seafood Restaurant         Cosmetics Shop  
2      Seafood Restaurant         Cosmetics Shop  
3      Seafood Restaurant         Cosmetics Shop  
4      Seafood Restaurant         Cosmetics Shop  
..                    ...                    ...  
322    Seafood Restaurant         Cosmetics Shop  
323    Seafood Restaurant         Cosmetics Shop  
324    Seafood Restaurant         Cosmetics Shop  
325    Seafood Restaurant         Cosmetics Shop  
326    Seafood Restaurant         Cosmetics Shop  

[301 rows x 15 co

In [38]:
df_merged.loc[df_merged['Cluster Labels'] == 3, df_merged.columns[[1] + list(range(5, df_merged.shape[1]))]]

area_lat        lng         categories        CATEGORY GROUP  \
186  43.643556 -79.567659        Coffee Shop         Food/Beverage   
187  43.643556 -79.566191     Farmers Market                 Other   
188  43.643556 -79.560113      Grocery Store  Mall/Specialty Store   
189  43.643556 -79.560374         Restaurant         Food/Beverage   
190  43.643556 -79.567065       Intersection                 Other   
191  43.643556 -79.566218       Skating Rink                 Other   
192  43.643556 -79.560126     Clothing Store  Mall/Specialty Store   
193  43.643556 -79.563026  Convenience Store  Mall/Specialty Store   
194  43.643556 -79.563009              Hotel                 Other   
195  43.643556 -79.562990               Café         Food/Beverage   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
186               3          Skating Rink                  Café   
187               3          Skating Rink                  Café   
188               3          Skating Rink                  Café   
189               3          Skating Rink                  Café   
190               3          Skating Rink                  Café   
191               3          Skating Rink                  Café   
192               3          Skating Rink                  Café   
193               3          Skating Rink                  Café   
194               3          Skating Rink                  Café   
195               3          Skating Rink                  Café   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
186          Intersection           Coffee Shop            Restaurant   
187          Intersection           Coffee Shop            Restaurant   
188          Intersection           Coffee Shop            Restaurant   
189          Intersection           Coffee Shop            Restaurant   
190          Intersection           Coffee Shop            Restaurant   
191          Intersection           Coffee Shop            Restaurant   
192          Intersection           Coffee Shop            Restaurant   
193          Intersection           Coffee Shop            Restaurant   
194          Intersection           Coffee Shop            Restaurant   
195          Intersection           Coffee Shop            Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
186        Clothing Store        Farmers Market     Convenience Store   
187        Clothing Store        Farmers Market     Convenience Store   
188        Clothing Store        Farmers Market     Convenience Store   
189        Clothing Store        Farmers Market     Convenience Store   
190        Clothing Store        Farmers Market     Convenience Store   
191        Clothing Store        Farmers Market     Convenience Store   
192        Clothing Store        Farmers Market     Convenience Store   
193        Clothing Store        Farmers Market     Convenience Store   
194        Clothing Store        Farmers Market     Convenience Store   
195        Clothing Store        Farmers Market     Convenience Store   

    9th Most Common Venue 10th Most Common Venue  
186                 Hotel          Grocery Store  
187                 Hotel          Grocery Store  
188                 Hotel          Grocery Store  
189                 Hotel          Grocery Store  
190                 Hotel          Grocery Store  
191                 Hotel          Grocery Store  
192                 Hotel          Grocery Store  
193                 Hotel          Grocery Store  
194                 Hotel          Grocery Store  
195                 Hotel          Grocery Store

In [39]:
#Create chloropleth map
# create a plain toronto map
toronto_map2 = folium.Map(location=[center_latitude, center_longitude], zoom_start=11)
# generate choropleth map using the total immigration of each country to Canada from 1980 to 2013
toronto_map2.choropleth(
    geo_data=geojson_file,
    data=df_demographics,
    columns=['NeighbourhoodWithId', 'Total Population'],
    key_on='feature.properties.AREA_NAME',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Population Density'
)

borough_colors={'Central Toronto':'#66c2a5','Downtown Toronto':'#fc8d62','East York':'#8da0cb','Etobicoke':'#e78ac3',
                'North York':'#a6d854','Scarborough':'#ffd92f','West Toronto':'#e5c494'}
cluster_colors={0:'red',1:'blue',2:'green',3:'orange'}
for borough, lat, lng, categories, name, cluster in zip(df_merged['Borough'], df_merged['lat'], df_merged['lng'],
                                                         df_merged['categories'], df_merged['name'], df_merged['Cluster Labels']):
    label = '{}, {}, {}'.format(cluster, name, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
            [lat, lng],
            radius=7,
            popup=label,
            color=cluster_colors[cluster],
            fill=True,
            fill_color=borough_colors[borough],
            fill_opacity=0.9,
            parse_html=False).add_to(toronto_map2)
# display map
toronto_map2

/Users/gquisumbing/Documents/envs/dsclass/lib/python3.7/site-packages/folium/folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [42]:
df_merged.shape

(327, 19)